# AC 221 - Problem Set 3

## Problem 1

### Finding Duplicates

In [1]:
import numpy as np
import csv

We begin by reading in the csv with the `csv` Python functionality and using a modified version of [Jim's `find_dups` function](https://github.com/jimwaldo/APCOMP221Code/blob/master/find_duplicates.py) to find duplicates. We won't get rid of duplicates until we repair values. 

#### Useful Functions

In [23]:
def get_key(x):
    return (x['user_id'], x['course_id'])
    
# Jim's find_dups Function (Modified to not print out csv with unique values)
"""
Created on 2019-03-14
@author waldo
"""

def find_dups(csv_in):
    total_lines = 0
    unique_lines = 0
    dup_lines = 0
    lines_seen = set()

    for l in csv_in:
        total_lines += 1
        key = get_key(l)
        if key not in lines_seen:
            lines_seen.add(key)
            unique_lines += 1
        else:
            dup_lines += 1
    return total_lines, unique_lines, dup_lines

In [3]:
# Open original csv to get headers
with open("sample_set.csv", "r") as org_csv:
    reader = csv.reader(org_csv)
    headers = next(reader)

In [4]:
print(headers)

['course_id', 'user_id', 'registered', 'viewed', 'explored', 'certified', 'completed', 'ip', 'cc_by_ip', 'countryLabel', 'continent', 'city', 'region', 'subdivision', 'postalCode', 'un_major_region', 'un_economic_group', 'un_developing_nation', 'un_special_region', 'latitude', 'longitude', 'LoE', 'YoB', 'gender', 'grade', 'passing_grade', 'start_time', 'first_event', 'last_event', 'nevents', 'ndays_act', 'nplay_video', 'nchapters', 'nforum_posts', 'nforum_votes', 'nforum_endorsed', 'nforum_threads', 'nforum_comments', 'nforum_pinned', 'roles', 'nprogcheck', 'nproblem_check', 'nforum_events', 'mode', 'is_active', 'cert_created_date', 'cert_modified_date', 'cert_status', 'verified_enroll_time', 'verified_unenroll_time', 'profile_country', 'y1_anomalous', 'email_domain', 'language_brwsr', 'language_brwsr_country', 'language_brwsr_sec', 'language_brwsr_sec_country', 'language_brwsr_code', 'language_brwsr_subcode', 'language_brwsr_sec_code', 'language_brwsr_sec_subcode', 'language_brwsr_nev

In [5]:
# Run function
with open("sample_set.csv", "r", encoding = "utf8") as org_file:
    org_csv = csv.DictReader(org_file)        
    total_lines, unique_lines, dup_lines = find_dups(org_csv)

In [6]:
print("Total lines: {}".format(total_lines))
print("Unique lines: {}".format(unique_lines))
print("Duplicated lines: {}".format(dup_lines))

Total lines: 1100005
Unique lines: 137450
Duplicated lines: 962555


### Repairing Values

First we want to start by getting a better sense of our data to determine which values need to be repaired. This will also help us determine how to deal with missing values on a field by field basis. 

Then, we will be looking at all original records when trying to repair values. For example, if a duplicate records exist for a student/class pair, we can check if the duplicates have a better version of the bad value or an existing version of a missing value. 

In [7]:
# Read and store original records
original_records = []

with open("sample_set.csv", "r", encoding = "utf8") as org_file:
    org_csv = csv.DictReader(org_file)
    for row in org_csv:
        original_records.append(row)

#### Useful Functions

In [8]:
# Functions for exploring
def column_frequencies(theRecords, theColumn):
    frequency_dict = {}
    for record in theRecords:
        record_column = record[theColumn]
        if record_column in frequency_dict:
            frequency_dict[record_column] += 1
        else:
            frequency_dict[record_column] = 1
    return frequency_dict

def print_sorted_col_by_freq(frequencyDict):
    print({k: v for k, v in sorted(frequencyDict.items(), key=lambda item: item[1])})
    
def print_sorted_col_by_key(frequencyDict):
    for key in sorted(frequencyDict.keys()):
        print(key, frequencyDict[key])
        
def print_frequencies_col_group(colGroup):
    for col in colGroup:
        print(col)
        freqs = column_frequencies(original_records, col)
        print_sorted_col_by_key(freqs)
        print('')
        
def get_missing_frequency(theRecords, theColumn):
    freqs = column_frequencies(theRecords, theColumn)
    if '' in freqs.keys():
        return freqs['']
    else:
        return 0

def print_missing_frequencies(theRecords, colGroup):
    for col in colGroup:
        print("{}: {}".format(col, get_missing_frequency(theRecords, col)))

# Functions for repairing


#### Find Bad or Missing Values

In order to determine what values are missing, we need to take a deeper look at the possible values in each column. We will also calculate the frequency of missing (the string '') for each column. Only one column appeared to have another value that can possible be regarded as representing missing: 'null'. We will keep values as strings for now to make sure we are picking up any bad string values in expected numeric fields. 

In [9]:
# Take a look at columns by general categorical group
registration_cols = ['registered', 'viewed', 'explored', 'certified', 'completed', 'cert_status']
location_cols = ['cc_by_ip', 'countryLabel', 'continent', 'city', 'region', 'subdivision', 'postalCode', 
                 'profile_country', 'latitude', 'longitude']
un_cols = ['un_major_region', 'un_economic_group', 'un_developing_nation', 'un_special_region']
demo_cols = ['LoE', 'YoB', 'gender']
grade_cols = ['grade', 'passing_grade']
time_date_cols = ['start_time', 'first_event', 'last_event', 'cert_modified_date', 'cert_created_date', 'verified_enroll_time',
                  'verified_unenroll_time'] 
action_cols = ['nevents', 'ndays_act', 'nplay_video', 'nchapters'] 
forum_cols = ['nforum_posts', 'nforum_votes', 'nforum_endorsed', 'nforum_threads', 'nforum_comments', 'nforum_pinned', 
              'roles', 'nprogcheck', 'nproblem_check', 'nforum_events'] 
language_cols = ['language_brwsr', 'language_brwsr_country', 'language_brwsr_sec', 'language_brwsr_sec_country', 
                 'language_brwsr_code', 'language_brwsr_subcode', 'language_brwsr_sec_code', 'language_brwsr_sec_subcode', 
                 'language_brwsr_nevents', 'language_brwsr_ndiff', 
                 'language', 'language_download', 'language_nevents', 'language_ndiff']
video_cols = ['ntranscript', 'nshow_answer', 'nvideo', 'nvideos_unique_viewed', 'nvideos_total_watched', 'nseq_goto', 
              'nseek_video', 'npause_video']
dt_cols = ['avg_dt', 'sdv_dt', 'max_dt', 'n_dt', 'sum_dt']
roles_cols = ['roles_isBetaTester', 'roles_isInstructor', 'roles_isStaff', 'roles_isCCX', 'roles_isFinance', 'roles_isLibrary',
              'roles_isSales', 'forumRoles_isAdmin', 'forumRoles_isCommunityTA', 'forumRoles_isModerator', 
              'forumRoles_isStudent']
other_cols = ['mode', 'is_active', 'y1_anomalous', 'email_domain']

In [8]:
for registration_col in registration_cols:
    print(registration_col)
    print(column_frequencies(original_records, registration_col))

registered
{'True': 1100005}
viewed
{'True': 568803, 'False': 531202}
explored
{'False': 450525, 'True': 118278, '': 531202}
certified
{'False': 1080771, 'True': 19234}
completed
{'False': 1076712, 'True': 23293}
cert_status
{'': 582030, 'downloadable': 19234, 'notpassing': 488079, 'audit_notpassing': 10104, 'audit_passing': 312, 'unverified': 223, 'unavailable': 23}


In [23]:
print_missing_frequencies(original_records, registration_cols)

registered: 0
viewed: 0
explored: 531202
certified: 0
completed: 0
cert_status: 582030


In [2]:
explored_false_missing = 450525 + 531202
explored_false_missing

981727

Questions:
* Are there records where `certified` or `completed` are "True" but `explored` is "False" or Missing?
* `explored` missing values might be related to missing values for other variables 

In [11]:
print_frequencies_col_group(demo_cols)

LoE
 159905
a 49333
b 323862
el 4953
hs 234270
jhs 30482
m 227234
none 3340
other 20952
p 38673
p_oth 2794
p_se 4207

YoB
 167284
1893 7
1894 49
1895 58
1896 36
1897 79
1898 60
1899 48
1900 127
1901 8
1902 13
1903 1
1904 15
1906 17
1908 4
1909 18
1911 3
1914 7
1917 13
1918 23
1920 8
1921 2
1922 16
1923 28
1924 37
1925 15
1926 29
1927 15
1928 46
1929 103
1930 82
1931 171
1932 114
1933 175
1934 173
1935 156
1936 192
1937 289
1938 386
1939 447
1940 534
1941 592
1942 829
1943 800
1944 853
1945 829
1946 1432
1947 1603
1948 1848
1949 1685
1950 2076
1951 2264
1952 2007
1953 2498
1954 2638
1955 2865
1956 3015
1957 3619
1958 3344
1959 3840
1960 4782
1961 4095
1962 5047
1963 5244
1964 4901
1965 5867
1966 5901
1967 6520
1968 7663
1969 8264
1970 9366
1971 9417
1972 10101
1973 10113
1974 10901
1975 12178
1976 13498
1977 14990
1978 15742
1979 17283
1980 20633
1981 21318
1982 23088
1983 26641
1984 28479
1985 31868
1986 35181
1987 36568
1988 40677
1989 43797
1990 48874
1991 45994
1992 47820
1993 45917

Level of Education Questions:
* Probably don't want to impute, unless we do it at the course level. (Someone with a Ph.D probably isn't going to be taking an elementary school course.)

Year of Birth Questions:
* What's our cutoff for a reasonable value?
* For unreasonable or missing values, we can check if the same user supplied a more correct value in other records. 

Gender Questions
* Do we want to collapse "null" and missing? 
* Do we want to impute gender? (I'd rather not, given that it might not be missing randomly, especially at the course level.)
* For missing values, we can check if the same user supplied a more correct value in other records.

In [12]:
print_frequencies_col_group(grade_cols)

grade
 344317
0.0 688412
0.01 4570
0.02 2931
0.03 3155
0.04 3082
0.05 2707
0.06 2192
0.07 1263
0.08 1982
0.09 2161
0.1 1407
0.11 1053
0.12 673
0.13 1067
0.14 1102
0.15 789
0.16 527
0.17 1029
0.18 658
0.19 396
0.2 829
0.21 394
0.22 511
0.23 562
0.24 295
0.25 615
0.26 557
0.27 328
0.28 275
0.29 549
0.3 455
0.31 312
0.32 197
0.33 449
0.34 240
0.35 374
0.36 215
0.37 355
0.38 281
0.39 317
0.4 328
0.41 193
0.42 265
0.43 281
0.44 191
0.45 248
0.46 155
0.47 186
0.48 109
0.49 85
0.5 244
0.51 143
0.52 272
0.53 184
0.54 96
0.55 147
0.56 206
0.57 209
0.58 167
0.59 128
0.6 194
0.61 224
0.62 251
0.63 171
0.64 295
0.65 300
0.66 141
0.67 283
0.68 170
0.69 193
0.7 1006
0.71 471
0.72 355
0.73 462
0.74 277
0.75 549
0.76 287
0.77 405
0.78 370
0.79 339
0.8 506
0.81 397
0.82 322
0.83 480
0.84 365
0.85 509
0.86 440
0.87 659
0.88 532
0.89 492
0.9 788
0.91 557
0.92 827
0.93 779
0.94 796
0.95 816
0.96 965
0.97 965
0.98 992
0.99 710
1.0 2926
1.01 1
1.11 5
1.15 13

passing_grade
 27866
0.5 70116
0.55 970
0.58 767

In [24]:
print_missing_frequencies(original_records, grade_cols)

grade: 344317
passing_grade: 27866


Grade Questions:
* Looks like extra credit might have existed?
* Do we want to convert to numeric? Or just put a note that whoever starts doing analysis would have to do that?

Passing Grade Questions:
* This column looks okay?
* Documentation says it should be the same within a course. We could check if any courses have different values. 

In [28]:
print_missing_frequencies(original_records, time_date_cols)

start_time: 0
first_event: 255762
last_event: 255762
cert_modified_date: 582030
cert_created_date: 582030
verified_enroll_time: 1086144
verified_unenroll_time: 1099302


Time and Date Questions:
* How do we want to deal with checking these? Maybe RegEx to see that they follow the write date-time format?

In [13]:
print_frequencies_col_group(action_cols)

ndays_act
 255762
1 320058
10 11301
100 85
101 100
102 109
103 48
104 58
105 64
106 54
107 96
108 85
1083 1
109 37
11 9301
110 39
111 37
112 40
113 43
114 78
1146 6
115 52
116 48
1168 14
117 34
118 54
119 48
12 9568
120 67
121 46
122 49
123 33
124 30
125 38
126 45
127 19
128 60
129 29
13 7552
130 36
131 46
132 44
133 27
134 28
135 15
136 24
137 27
138 7
139 39
14 7001
140 7
141 40
142 36
143 27
144 26
145 33
146 35
147 24
148 40
149 9
1494 4
15 6482
150 23
1508 4
151 29
153 32
154 18
156 21
157 38
158 11
159 19
16 5551
160 12
162 12
163 12
164 13
165 14
166 38
167 31
168 6
169 16
17 4900
170 15
171 9
172 28
173 10
174 16
175 12
176 27
177 4
178 38
179 6
18 4174
180 39
181 9
184 10
1840 1
185 10
186 24
187 14
188 31
189 1
19 3947
190 37
191 5
1919 14
192 25
193 10
195 2
196 26
197 11
198 17
199 9
2 151227
20 3284
201 27
203 13
204 15
205 5
206 8
207 25
208 18
209 14
21 2972
210 2
212 6
213 13
215 19
216 12
217 22
218 27
22 3367
220 5
221 50
223 2
224 2
225 4
229 10
23 2720
230 14
235 10

824 15
825 25
826 29
8261 2
827 3
828 15
829 9
83 437
830 23
8311 13
8318 4
832 23
833 23
834 11
835 2
836 11
837 14
8373 1
838 16
839 13
84 711
840 10
841 22
842 6
843 12
844 11
845 13
846 29
848 7
85 602
852 12
853 41
854 11
855 1
856 11
857 8
858 2
86 604
860 5
862 23
863 11
864 29
865 13
866 26
867 14
868 26
87 603
874 9
876 28
877 6
879 10
88 714
880 16
882 18
883 8
885 10
886 5
8869 8
887 8
889 6
89 518
892 20
893 14
894 11
895 49
897 11
899 8
9 7497
90 634
900 18
90057 15
902 3
903 21
904 15
905 1
907 14
908 2
909 11
91 532
910 12
911 2
913 12
914 3
915 18
916 33
917 3
92 554
921 38
922 19
924 13
925 15
926 36
927 2
928 4
929 6
93 578
931 15
932 14
934 12
935 16
936 8
937 12
938 33
939 8
94 534
941 21
944 2
946 22
948 20
95 480
9506 1
951 18
952 15
954 18
955 7
956 11
957 8
958 3
96 532
961 8
963 21
965 1
966 3
967 2
968 30
969 18
97 516
970 13
971 26
972 23
973 27
974 15
976 10
98 516
980 24
984 8
9841 6
985 3
986 14
9868 6
987 13
988 2
989 3
99 534
990 12
991 5
993 28
995 14
9

In [25]:
print_missing_frequencies(original_records, action_cols)

nevents: 255798
ndays_act: 255762
nplay_video: 255798
nchapters: 531202


Action Questions:
* These look fine. 

In [17]:
print_frequencies_col_group(forum_cols)

nforum_posts
 1069957
1 11984
10 461
104 12
105 9
107 5
109 4
11 348
119 13
12 257
123 8
126 9
13 372
130 6
134 3
138 12
139 3
14 180
144 1
148 6
15 215
156 12
159 12
16 181
165 7
17 139
18 187
19 241
2 4248
20 97
21 95
22 131
23 114
24 164
25 114
26 43
267 6
27 75
28 99
285 12
29 148
299 15
3 2358
30 65
31 80
32 144
33 79
34 45
35 56
36 63
37 56
38 80
39 53
4 1903
40 20
41 57
42 48
43 46
44 3
45 23
46 7
47 26
48 33
49 27
5 1203
50 46
51 2
52 64
53 32
54 16
55 24
56 7
57 10
59 31
6 971
60 5
61 13
63 14
64 3
66 8
67 14
69 16
7 777
71 16
72 20
75 25
76 8
8 632
81 12
84 5
85 10
86 10
89 10
9 677
90 25
91 7
96 3
97 12

nforum_votes
 1069957
0 20843
1 3896
10 123
11 122
110 6
114 6
115 3
12 105
123 7
13 48
135 11
137 14
138 15
14 87
15 20
16 73
169 9
17 43
18 65
19 14
2 1562
20 15
208 6
21 19
22 8
224 15
23 2
24 2
25 25
26 61
27 8
28 21
29 20
3 698
30 12
31 13
32 4
33 18
35 13
38 10
39 26
4 563
40 15
41 15
44 23
47 13
48 9
5 494
53 4
6 190
61 35
62 14
66 1
7 225
70 12
8 198
81 12
82 6
83 12

 255798
0 788895
1 11377
10 1098
100 49
1007 4
1009 3
101 54
1019 5
102 41
103 44
104 76
1044 14
105 40
106 57
1060 6
1068 2
107 25
108 32
109 38
11 919
110 81
1102 14
111 50
112 18
113 30
1135 2
114 11
115 44
116 5
117 26
118 38
119 61
1196 3
12 701
120 49
121 39
122 42
123 15
124 35
1247 1
125 11
126 49
127 11
128 51
129 71
13 770
130 1
131 12
132 45
133 33
134 37
1344 10
135 12
136 17
137 22
138 15
139 5
14 716
140 5
1402 14
141 51
142 6
143 27
1434 1
144 18
145 10
1454 2
146 36
147 2
148 40
1484 15
149 63
15 610
150 21
151 23
152 20
153 49
154 19
155 58
156 8
157 15
158 26
159 23
16 708
160 2
161 15
162 29
1625 12
163 30
1634 6
1639 6
164 15
165 5
166 49
167 30
1681 9
169 17
17 444
170 6
171 8
1718 8
172 10
173 14
174 15
175 13
176 11
177 14
178 26
17829 12
179 37
18 596
181 14
182 30
184 7
1844 14
185 16
186 9
188 16
189 19
1899 2
19 566
191 8
192 15
194 13
195 16
197 31
198 9
2 6664
20 385
200 10
201 7
202 26
203 5
206 1
208 22
21 434
210 35
211 29
212 5
213 12
214 15
215 7
216 5

In [30]:
print_missing_frequencies(original_records, forum_cols)

nforum_posts: 1069957
nforum_votes: 1069957
nforum_endorsed: 1069957
nforum_threads: 1069957
nforum_comments: 1069957
nforum_pinned: 1069957
roles: 0
nprogcheck: 255798
nproblem_check: 255798
nforum_events: 255798


Forum Questions
* Really high values might be of from an administrator? 

In [21]:
print_frequencies_col_group(language_cols)

language_brwsr
 679476
Afrikaans 14
Albanian 14
Arabic 2130
Bengali 13
Bokmål, Norwegian; Norwegian Bokmål 792
Bosnian 4
Bulgarian 357
Burmese 2
Catalan; Valencian 196
Chinese 12358
Croatian 260
Czech 617
Danish 800
Dutch; Flemish 3475
English 314603
Estonian 90
Finnish 347
French 8412
Galician 4
Georgian 12
German 5780
Greek, Modern (1453-) 1945
Hebrew 375
Hindi 19
Hungarian 838
Icelandic 15
Indonesian 386
Italian 2646
Japanese 1408
Kinyarwanda 3
Korean 2566
Latin 5
Latvian 82
Lithuanian 240
Malayalam 10
Mongolian 23
Persian 22
Polish 2410
Portuguese 14625
Romanian; Moldavian; Moldovan 701
Russian 8056
Serbian 289
Slovak 264
Slovenian 181
Spanish; Castilian 27123
Swedish 964
Thai 415
Turkish 2929
Ukrainian 731
Vietnamese 978

language_brwsr_country
 691292
Albania 14
Argentina 2002
Australia 1832
Austria 156
Bangladesh 13
Belgium 159
Bolivia 23
Bosnia and Herzegovina 4
Brazil 13144
Bulgaria 357
Canada 2439
Chile 141
China 8933
Colombia 333
Costa Rica 66
Croatia 260
Czech Republic 466


2221 13
2222 44
2224 4
2225 13
2227 8
2228 6
2229 15
223 306
2230 11
2235 12
2236 25
2237 12
2238 6
2239 2
224 326
2240 34
2241 3
2242 1
2244 15
2245 2
2246 4
2247 46
2249 7
225 261
2250 4
2251 10
2252 1
2255 25
2256 24
2257 22
2258 14
2259 4
226 325
2263 24
2264 37
2265 4
2266 7
2267 5
2268 2
2269 6
227 231
2271 16
2272 13
2273 15
2274 26
2275 5
22754 6
2278 16
2279 12
228 375
2280 26
2285 6
2286 13
229 322
2291 6
2292 11
2293 25
2294 11
2296 32
2297 15
2299 15
23 3425
230 385
2300 11
2301 16
2304 15
2307 13
231 364
2310 9
2312 14
2313 8
2314 14
2315 8
2316 15
232 399
2321 13
2322 10
23222 1
2323 7
2324 6
2328 13
2329 18
233 303
2331 6
2332 14
2336 15
23361 8
2337 14
2338 6
2339 4
234 400
2343 35
2344 8
2345 27
2347 20
2348 6
235 307
2350 8
2351 7
2353 9
2354 5
2355 10
2356 7
2357 8
2358 6
236 237
2360 3
2361 3
2362 4
2364 12
2365 13
2366 4
2367 9
2368 7
2369 14
237 288
2371 11
2372 5
2373 12
2374 7
2375 37
2376 12
2377 15
2379 6
238 290
2380 22
2383 11
2384 13
2385 3
2386 6
2387 11
2

4683 9
469 118
4692 14
4699 15
47 1927
470 90
4706 10
4707 10
471 95
4718 14
472 99
4720 13
473 140
4731 5
4732 12
474 143
4740 5
4746 12
4749 2
475 151
4753 6
476 131
4763 2
4768 5
477 139
4779 11
478 124
4788 13
4789 4
479 134
48 2298
480 158
4801 8
481 104
4810 26
4814 12
4816 11
482 130
4822 13
4825 6
483 78
4830 14
4838 10
484 182
4841 8
485 118
4859 16
486 117
4866 9
4868 11
487 98
488 110
4880 7
489 144
4892 12
48937 9
49 1606
490 71
491 71
4914 13
492 115
4923 2
493 159
4934 8
494 184
4947 14
495 175
4950 3
4957 14
496 96
4961 7
497 108
4977 1
498 125
499 149
4991 4
4992 17
4998 3
5 14056
50 2146
500 130
5000 1
501 141
5019 14
502 130
5028 8
503 178
504 104
5048 7
505 56
5053 3
5054 15
5055 12
5057 12
506 90
5062 9
5068 1
507 103
5071 10
5074 4
5075 14
5079 3
508 87
5088 14
509 62
51 1681
510 110
5100 14
511 62
5110 14
5113 12
5114 8
512 150
513 102
5130 22
5132 7
514 114
5141 5
515 89
516 85
5165 5
5169 22
517 101
5175 12
5177 5
518 117
5185 2
519 64
52 1901
520 109
521 107
52

 711897
1 374764
10 14
2 9343
3 2546
4 800
5 367
6 168
7 63
8 15
9 28



In [31]:
print_missing_frequencies(original_records, language_cols)

language_brwsr: 679476
language_brwsr_country: 691292
language_brwsr_sec: 973180
language_brwsr_sec_country: 1037322
language_brwsr_code: 679436
language_brwsr_subcode: 679436
language_brwsr_sec_code: 956573
language_brwsr_sec_subcode: 1034721
language_brwsr_nevents: 524597
language_brwsr_ndiff: 524597
language: 711897
language_download: 711897
language_nevents: 711897
language_ndiff: 711897


Language Questions
* Crosstab of code and language?

In [22]:
print_frequencies_col_group(video_cols)

ntranscript
 255798
0 723554
1 35767
10 1723
100 83
101 59
102 76
103 78
104 61
105 51
106 35
107 54
108 57
109 54
11 1517
110 66
111 37
112 47
113 100
114 52
115 26
116 51
117 28
118 19
119 58
1194 9
12 1700
120 84
121 36
122 52
123 38
124 81
125 36
126 43
127 81
128 78
129 12
1294 3
13 1345
130 43
131 84
132 70
133 29
134 37
135 13
136 62
137 53
138 50
139 40
14 1421
140 31
1408 7
141 46
142 7
143 25
144 50
145 25
1450 7
146 35
147 25
148 63
149 13
15 902
150 37
151 32
152 34
153 51
154 43
155 14
156 20
157 51
158 22
159 26
16 920
160 12
161 12
162 26
163 13
164 12
165 41
166 29
167 55
168 15
17 748
170 20
171 48
172 21
173 7
174 49
175 17
176 56
177 28
178 32
179 38
18 956
180 3
181 3
182 27
183 6
184 13
185 12
186 32
187 59
188 15
189 24
19 561
190 18
191 26
192 16
194 2
195 4
196 24
197 16
198 4
1989 13
199 38
2 18955
20 623
201 12
202 8
203 21
204 24
205 47
207 3
208 17
21 752
210 17
211 14
213 23
214 14
216 5
217 25
218 5
22 660
221 15
222 13
223 1
224 7
225 4
226 30
227 7
228 9

697 6
698 20
699 26
7 8449
70 910
700 12
701 26
703 19
704 36
705 18
706 38
707 47
708 17
709 11
71 783
710 24
711 13
712 11
713 17
714 12
715 16
716 15
717 3
718 13
72 955
720 9
721 13
722 8
723 16
724 20
7248 15
725 38
7251 6
726 12
728 18
729 18
73 691
731 21
7314 9
732 5
733 35
736 10
737 5
738 19
739 37
74 783
740 12
742 20
743 3
744 26
7448 10
745 13
746 4
747 18
748 5
75 754
750 32
752 9
754 5
755 1
756 3
758 23
759 27
76 687
760 20
761 11
762 40
763 17
7637 7
764 20
766 26
767 29
768 10
769 7
77 684
770 14
771 36
772 19
773 16
774 12
7745 12
775 30
776 6
779 16
78 741
780 29
783 30
784 27
785 34
786 15
787 13
788 17
79 688
790 1
791 10
792 8
793 13
794 26
795 29
7956 3
796 5
798 26
799 11
8 9142
80 612
800 43
801 38
802 31
803 11
805 30
806 5
807 16
808 1
809 30
81 718
810 16
811 16
813 34
814 15
815 4
817 34
818 21
82 622
820 1
821 10
822 7
823 14
824 15
825 25
826 29
8261 2
827 3
828 15
829 9
83 437
830 23
8311 13
8318 4
832 23
833 23
834 11
835 2
836 11
837 14
8373 1
838 16


0.3142857142857143 74
0.3146067415730337 28
0.31512605042016806 34
0.31521739130434784 9
0.3157894736842105 247
0.3162393162393162 7
0.31666666666666665 17
0.3170731707317073 15
0.3173076923076923 10
0.3177570093457944 57
0.3183856502242152 15
0.31840796019900497 28
0.3191489361702128 25
0.31932773109243695 51
0.3194444444444444 19
0.32 11
0.32075471698113206 11
0.32098765432098764 26
0.32142857142857145 184
0.32222222222222224 8
0.3225806451612903 9
0.32286995515695066 11
0.32323232323232326 2
0.32338308457711445 40
0.3235294117647059 14
0.32432432432432434 215
0.3246753246753247 6
0.3247863247863248 2
0.325 38
0.3251121076233184 15
0.32558139534883723 14
0.3258426966292135 14
0.3259668508287293 7
0.32608695652173914 40
0.3262411347517731 11
0.32653061224489793 16
0.3269230769230769 33
0.32710280373831774 15
0.32727272727272727 13
0.3273542600896861 14
0.3275862068965517 14
0.3277310924369748 91
0.32786885245901637 15
0.3283582089552239 15
0.3287671232876712 45
0.3295964125560538 1
0.

0.8598130841121495 1
0.8603896103896104 13
0.8604651162790697 7
0.8617886178861789 1
0.8620689655172413 32
0.8625 7
0.8631578947368421 12
0.8636363636363636 4
0.8641975308641975 9
0.8651685393258427 25
0.8653846153846154 22
0.8666666666666667 20
0.8668831168831169 16
0.8679245283018868 31
0.868421052631579 31
0.8688524590163934 1
0.8695652173913043 86
0.8699186991869918 1
0.8709677419354839 20
0.8715596330275229 9
0.8723404255319149 12
0.8732394366197183 8
0.8736842105263158 23
0.875 382
0.8766233766233766 9
0.8771929824561403 6
0.8775510204081632 24
0.8784530386740331 14
0.8793103448275862 73
0.8798701298701299 6
0.8805970149253731 20
0.8807339449541285 23
0.8809523809523809 5
0.8817204301075269 5
0.8823529411764706 119
0.8825503355704698 1
0.8831168831168831 24
0.8833333333333333 15
0.8840579710144928 9
0.8846153846153846 68
0.8854166666666666 1
0.8855721393034826 12
0.8857142857142857 46
0.8859060402684564 15
0.8861788617886179 7
0.8863636363636364 3
0.8867924528301887 25
0.88732394

 255798
0 608304
1 20260
10 5860
100 261
1002 14
1003 12
1004 2
101 258
1014 12
1016 12
1017 10
102 305
1029 10
103 166
1033 11
1035 14
1038 10
10398 14
104 214
1041 10
1043 4
1045 7
1048 10
105 388
106 225
1060 1
1062 5
1066 2
1068 9
107 235
1077 12
1078 15
108 259
1080 15
1081 4
1088 1
109 213
1094 12
1096 12
1098 2
11 4743
110 227
1100 13
1105 15
1106 8
1107 8
1109 17
111 206
1112 3
1116 14
1117 6
112 225
1120 3
1123 4
1127 6
113 329
1132 14
114 213
1145 5
1147 3
1149 8
115 236
1151 14
1157 12
116 153
117 237
1173 14
1177 6
118 184
119 188
1190 12
1193 13
1197 10
12 4864
120 216
1204 8
1209 6
121 147
1217 1
1218 9
122 66
1221 2
1229 13
123 141
124 119
1240 10
1241 7
1244 1
1247 4
1249 17
125 148
126 231
1263 6
1266 11
1269 21
127 115
128 170
1281 9
1288 2
129 164
1296 10
13 3885
130 151
1302 5
131 169
132 129
1320 2
1322 30
1323 12
133 131
1339 4
134 162
1347 8
135 180
1355 10
136 124
137 148
1372 14
1378 2
138 209
1380 6
1389 10
139 213
1399 7
14 4039
140 143
141 189
142 146
143 15

In [32]:
print_missing_frequencies(original_records, video_cols)

ntranscript: 255798
nshow_answer: 255798
nvideo: 255798
nvideos_unique_viewed: 729106
nvideos_total_watched: 729106
nseq_goto: 255798
nseek_video: 255798
npause_video: 255798


Videos Questions
* Most variables have same missing value: 255798
* Some have missing value: 729106
* `nvideos_total_watched` is mostly from 0 to 1, but goes up to 6.5. Thought it was total fraction of videos watched. If > 1, does that count repeats?

In [ ]:
print_frequencies_col_group(dt_cols)

avg_dt
 439584
0.0 50
0.000274 15
0.000275 15
0.000277 10
0.000282 8
0.000284 36
0.000289 11
0.000295 8
0.000296 12
0.000297 15
0.000298 12
0.000304 8
0.000306 13
0.000312 8
0.000316 2
0.000317 1
0.00032 11
0.000322 10
0.000325 7
0.000327 1
0.000328 12
0.000331 10
0.000333 12
0.000334 13
0.000336 15
0.000339 21
0.000341 22
0.000342 22
0.000343 12
0.000344 14
0.000345 2
0.000348 5
0.000353 6
0.000354 8
0.000357 15
0.00036 14
0.000364 22
0.000369 14
0.000372 2
0.000376 15
0.000377 7
0.000378 12
0.00038 7
0.000384 5
0.000389 15
0.000393 8
0.000398 9
0.000401 6
0.000402 13
0.000403 8
0.000409 11
0.00041 3
0.000412 10
0.000423 5
0.000425 16
0.000427 7
0.000436 3
0.000439 23
0.00044 11
0.000445 25
0.000447 11
0.00045 13
0.000455 6
0.00046700000000000024 7
0.000472 11
0.000475 5
0.000478 13
0.000479 8
0.0004819999999999999 10
0.000483 1
0.000486 9
0.0004900000000000003 7
0.000491 3
0.0004939999999999999 5
0.000494 1
0.0004970000000000005 1
0.0005 1
0.000507 11
0.00051 7
0.000516 4
0.000517 4


1.716562 4
1.7169681490919526 8
1.7171295272727265 15
1.7172727307692301 5
1.7175955156249998 10
1.71892 4
1.7189576000000002 1
1.7191696714975846 1
1.7195356000000002 6
1.7199359628571433 5
1.7291717000000002 8
1.7301229374999998 6
1.7308859999999993 5
1.7313985342465759 11
1.7323340000000005 3
1.7331978090277769 8
1.733475 8
1.734172 11
1.73569 6
1.7381856312499997 12
1.738835 9
1.740064 9
1.7440395 8
1.74568 4
1.7457004999999999 4
1.746999363636363 2
1.748863 15
1.749757 12
1.7502137777777778 12
1.7505 1
1.751725928619886 12
1.7517934444444445 9
1.754918645129221 7
1.755624488518517 12
1.756946 9
1.758691 12
1.7592521111111108 5
1.759579 8
1.7605620909090904 1
1.7622250000000006 12
1.7630147647058825 11
1.7651721111111105 1
1.7668081999999998 10
1.769927181818182 4
1.769964 5
1.7706209166666658 7
1.7732428484848486 14
1.773697 2
1.774271500000001 12
1.7745690000000003 15
1.778201 3
1.7804580000000012 6
1.7823260588235297 5
1.7829632499999999 15
1.7853692173913043 4
1.789068047619047

10.332370333333332 11
10.332512692307692 10
10.332625933963657 12
10.333029600000001 7
10.333233041420119 15
10.333859000000002 11
10.334357254949493 4
10.334515284375001 6
10.334733844049223 9
10.335003228915664 14
10.335203727272729 2
10.335964298507461 10
10.336158994416657 7
10.336219225081129 13
10.33659959791453 7
10.33666258333333 13
10.337299444444445 5
10.337367395238097 1
10.337522 14
10.338351 2
10.338427999999995 5
10.338618 8
10.338832 1
10.338952129545456 4
10.34024621785714 1
10.341148373015873 10
10.341500400000003 14
10.341692982123554 2
10.342069724358975 11
10.342747718064862 6
10.343003326379257 10
10.343136180555556 14
10.343563140598919 10
10.343630435897438 7
10.343881227722772 2
10.34391219899489 7
10.344115555555554 1
10.344573999999998 6
10.344718625 12
10.344734441145707 2
10.345121656914758 6
10.3452904 8
10.345559206896551 1
10.345596129040882 10
10.34583572767857 8
10.346223928571428 2
10.346924 2
10.347511127063633 11
10.34758637209302 14
10.3484134732142

10.754822518072288 15
10.755292230876067 3
10.755879820833334 14
10.755998212121213 12
10.756143595541493 14
10.756340240740741 12
10.757413737256995 7
10.758069789042391 2
10.75832300161943 5
10.75841928125 9
10.75862769984235 9
10.758631 8
10.759016866567462 12
10.75981033333333 8
10.75995692727273 10
10.760035406779664 13
10.760094790423416 8
10.760907330128205 8
10.76105112631579 5
10.7618475 6
10.761999512371206 6
10.762584669312169 7
10.762664555555554 12
10.763843059344559 9
10.763863650000001 10
10.765000494764045 9
10.765321 4
10.7657435 8
10.7659073 5
10.766079125000001 8
10.766365936111104 7
10.766416025 7
10.766650250000001 10
10.766945 2
10.767350025356123 9
10.767917706018517 9
10.768152076923078 7
10.768309339749537 12
10.7684515 12
10.77025839583333 7
10.771897467211703 4
10.772554174145302 4
10.773327392898551 3
10.77360621365729 7
10.773877052136752 14
10.774547083333335 2
10.775020699141438 7
10.77542166 10
10.7756715 12
10.775825000000001 4
10.776079254238693 3
10.7

11.129878000000001 13
11.13008200677966 6
11.130137382857145 13
11.130464374999999 13
11.13062462066633 1
11.130727315573768 10
11.130930142857142 3
11.131121218630984 3
11.131170928571427 6
11.132006268003481 12
11.132205444444445 3
11.132512631578948 8
11.132554593828893 5
11.132781070919355 5
11.13284875 15
11.133064341882235 15
11.13338293584724 7
11.133458000000001 14
11.133572000000001 5
11.133960764705883 8
11.134354666666667 8
11.134479779874214 9
11.134599721208305 14
11.134706327600739 2
11.135798699999999 15
11.13610672401323 9
11.136117394537036 14
11.136788041666666 10
11.136943 15
11.137164566666668 6
11.137342733333334 8
11.137408242801099 2
11.137656554076953 11
11.137732764908007 4
11.1398885 9
11.140493379629632 3
11.140624491071428 6
11.140661960526316 8
11.14084123076923 5
11.14194007705545 9
11.143401153846154 14
11.143826500000001 15
11.14485547385621 5
11.14497159654195 13
11.14502632 6
11.146624999999998 2
11.146711999999999 15
11.147132909357499 9
11.1472887058

...

106.96719060662305 15
107.00640533843996 10
107.01364035289782 15
107.0677410406292 7
107.20293092939231 5
107.21513478755057 7
107.25168807788263 4
107.25175559167863 1
107.26038941897528 8
107.27866838936954 9
107.29285027176792 10
107.30620599355206 14
107.34098919676477 2
107.34714900149523 4
107.36759287606294 8
107.39579460574794 15
107.42232223050996 2
107.46572936155619 2
107.4706063099565 13
107.51398962505104 2
107.5523700837412 8
107.59799583922792 12
107.65393152166885 1
107.68088713875932 9
107.75643013499085 10
107.81147688836614 8
107.82626540724495 9
107.88564617070784 1
107.89384629224271 13
107.89554442501037 2
107.91767112498998 8
107.92543755227199 6
107.92681798178614 2
107.9498394388835 9
107.98347227256467 6
108.0296487515246 8
108.12333507405663 3
108.12518590135853 11
108.15324000017623 13
108.15507380013659 8
108.2014403107609 12
108.22229214550303 1
108.22976392841296 13
108.23070013779126 3
108.24511326684983 1
108.2514791776632 15
108.26374149144849 10
108.

12.050685866304276 3
12.0507633736749 4
12.052469759636207 5
12.053513476034313 3
12.053988206531313 1
12.054401682563094 9
12.054927874973878 7
12.055027264576607 1
12.055621431514844 12
12.056630602371175 13
12.057504032555157 13
12.058772885280108 15
12.061712853638841 6
12.06458987931393 2
12.066850190924635 11
12.067080400753337 7
12.06810550725367 10
12.071686572710885 8
12.072297987095947 7
12.072385077150809 10
12.072646399723755 11
12.073653165814116 4
12.074909037413523 13
12.074947126229052 11
12.078160715210545 13
12.078296937125854 3
12.078927106375879 13
12.079579989154757 6
12.080886185327476 10
12.08121815897845 12
12.08167626511107 4
12.081886375113356 6
12.08190074765513 7
12.083485128158193 7
12.084697436022422 15
12.084729362904211 10
12.087113611975358 2
12.087236791875343 2
12.087258469165445 14
12.088180561294255 3
12.092399235164727 3
12.093300802620126 11
12.09420347732517 1
12.094386429634199 9
12.094797158282564 10
12.095069852857321 12
12.096345961118598 15


13.211098358452775 9
13.21166283427183 5
13.212051808307754 15
13.21424045245905 11
13.215692652217426 9
13.216490728770548 1
13.217655764810962 14
13.218135867795702 6
13.219897141309213 15
13.220136069675851 3
13.223423344020576 8
13.224347057203246 13
13.22448105513741 4
13.226380723299345 14
13.226486679277455 5
13.226924541919184 4
13.227121268565615 11
13.227616591735604 6
13.228321154099108 6
13.228368681942285 12
13.228468300718992 10
13.22848586996273 11
13.228533226627999 14
13.22898024808962 5
13.232131651319595 11
13.234166241145354 12
13.234704937780267 6
13.234713976715629 14
13.234962878302605 4
13.235387580329848 2
13.235715494031407 5
13.23676144781651 8
13.23854724212919 9
13.241202660343976 7
13.244135580910951 14
13.2450547062837 3
13.245671319267558 5
13.24796925252161 2
13.248426701502108 3
13.250409075827418 6
13.250422824712983 4
13.251857073518716 8
13.252038392833867 15
13.252234557403158 7
13.252430030142863 1
13.252500965730016 6
13.255406756320243 11
13.256

14.051052500214853 15
14.052694065190526 12
14.053540951909653 4
14.055849325908746 10
14.056464687442734 8
14.0566208834281 12
14.057946494065579 5
14.058034398266964 13
14.059054742053648 8
14.060191844351738 2
14.061709994572862 6
14.062890093267173 12
14.064579001064807 10
14.064590552274408 10
14.065409554761981 2
14.066624057409943 11
14.068922118124274 5
14.070083564048383 5
14.070104892810187 6
14.070437824545762 3
14.070523874634008 2
14.070848817943885 12
14.070997146009676 10
14.071189418627432 11
14.071938870030221 7
14.072362354119278 2
14.073527815625463 1
14.074449700443449 12
14.076580429273854 11
14.078071944508302 12
14.078286518657219 14
14.07910889131307 5
14.080094724192918 5
14.081098084073513 14
14.081111407847702 15
14.081127138346714 11
14.081918163885156 1
14.082094084646254 15
14.085667747942518 7
14.088843325040813 12
14.089884675241953 4
14.090673079127678 4
14.090834319649085 11
14.090918750876924 10
14.090954434591573 7
14.092318853741755 3
14.09262922153

15.327701062086328 14
15.327776269201086 10
15.328305127851042 13
15.329983757825367 4
15.330301835409838 6
15.33057676364315 10
15.331118877849809 7
15.331121043146235 6
15.332132002973319 1
15.335098459613071 2
15.335863359559946 11
15.33589130783894 1
15.336497829803228 8
15.336606614372545 12
15.338876232175865 3
15.339847291074818 1
15.341227363691242 3
15.341407675130258 14
15.341453190150377 4
15.343708612798627 6
15.344794808337609 15
15.344919723527104 12
15.346135058757445 5
15.347981869571736 5
15.348696880883084 15
15.349284048909512 3
15.349818758035127 10
15.351719554696473 6
15.351756097421333 14
15.352105460758109 11
15.353615973633104 12
15.353646645723396 5
15.354414667782775 14
15.35472224272092 2
15.357336599420053 5
15.358431738284821 4
15.361262951693705 4
15.361431650698838 15
15.362237649817823 2
15.365471810161331 10
15.366256705199813 10
15.367525171125415 15
15.36999329519015 5
15.37058460705503 3
15.370880027146283 3
15.371112643627775 10
15.37270030347502 6

In [33]:
print_missing_frequencies(original_records, dt_cols)

avg_dt: 439584
sdv_dt: 491752
max_dt: 439584
n_dt: 255762
sum_dt: 439584


Time Difference Questions
* Nothing looks weird, but not sure what bounds should be. 

In [35]:
print_frequencies_col_group(roles_cols)

roles_isBetaTester
 1099923
1 82

roles_isInstructor
 1099517
1 488

roles_isStaff
 1099522
1 483

roles_isCCX
 1100005

roles_isFinance
 1100002
1 3

roles_isLibrary
 1100005

roles_isSales
 1100002
1 3

forumRoles_isAdmin
 1099869
1 136

forumRoles_isCommunityTA
 1100005

forumRoles_isModerator
 1099871
1 134

forumRoles_isStudent
 62
1 1099943



Roles Questions:
* 1 or missing, no "true" missing
* No one has role of CCX, Library, or CommunityTA 

In [59]:
get_missing_frequency(original_records, 'ip')

165581

IP Address Questions
* Similar to above.

In [40]:
print_frequencies_col_group(location_cols)

cc_by_ip
 185572
AD 19
AE 3430
AF 221
AG 66
AI 39
AL 835
AM 639
AO 259
AR 5136
AS 7
AT 2598
AU 17860
AW 94
AZ 587
BA 710
BB 218
BD 3281
BE 4824
BF 184
BG 1943
BH 463
BI 39
BJ 123
BM 46
BN 132
BO 1041
BR 31705
BS 233
BT 175
BW 229
BY 1008
BZ 134
CA 34752
CD 234
CG 23
CH 3917
CI 381
CL 5044
CM 734
CN 20049
CO 10743
CR 1652
CU 138
CV 34
CW 77
CY 583
CZ 2325
DE 17595
DJ 90
DK 2767
DM 18
DO 1260
DZ 1610
EC 2190
EE 735
EG 10057
ES 14330
ET 1249
FI 1928
FJ 284
FM 15
FO 14
FR 12750
GA 40
GB 39756
GD 58
GE 922
GF 1
GG 50
GH 3103
GI 17
GL 19
GM 88
GN 39
GP 1
GQ 27
GR 7957
GT 1149
GU 67
GW 4
GY 300
HK 6641
HN 491
HR 1249
HT 634
HU 3022
ID 7755
IE 3761
IL 3124
IM 60
IN 85334
IQ 721
IR 1971
IS 346
IT 7384
JE 74
JM 770
JO 1295
JP 7643
KE 3229
KG 260
KH 646
KI 8
KM 5
KN 10
KR 7148
KW 417
KY 53
KZ 1049
LA 99
LB 963
LC 64
LK 1565
LR 128
LS 118
LT 1244
LU 355
LV 683
LY 173
MA 3522
MC 31
MD 460
ME 136
MG 160
MH 17
MK 472
ML 104
MM 599
MN 787
MO 247
MP 8
MQ 21
MR 34
MT 263
MU 664
MV 154
MW 370
MX 16574
MY

Busto Arsizio 15
Busto Garolfo 5
Butler 40
Butte 31
Butterworth 5
Buxton 6
Buzau 15
Bydgoszcz 104
Byron 14
Byron Center 13
Bytom 14
Béchar 6
Békéscsaba 19
Bénin 23
Béziers 5
Bühl 10
Cabedelo 11
Cabestany 18
Cabimas 19
Cabinda 11
Cabo Frio 26
Cabo Rojo 10
Cabo San Lucas 23
Caboolture 17
Cabot 27
Cabreúva 15
Cacak 4
Cachan 9
Cachoeira Paulista 11
Cachoeirinha 7
Cachoeiro De Itapemirim 15
Cacoal 10
Cacém 19
Cadenazzo 8
Cadereyta Jiménez 4
Cadiz 41
Cadolive 1
Cadro 8
Caen 32
Cafelândia 2
Cagayan De Oro City 139
Cagliari 65
Cagnes-sur-mer 3
Cagua 11
Caguas 85
Cahagnes 1
Cahors 17
Caieiras 20
Cainta 8
Cairnlea 2
Cairns 13
Cairo 4929
Cajamarca 14
Cajàzeiras 14
Cakovec 15
Calabasas 55
Calafell 15
Calamba 36
Calamba City 4
Calarasi 9
Calcutta 52
Caldas Da Rainha 28
Caldwell 111
Caledonia 8
Calexico 35
Calgary 1184
Calhoun 19
Cali 488
Calicut 172
Califon 15
California 11
Calne 6
Caloocan 82
Caloocan City 4
Caluire 7
Calumet City 26
Calumpit 27
Calvisson 4
Camabatela 15
Camarate 4
Camarillo 57
Ca

Duino 9
Duisburg 60
Duiven 9
Dulles 20
Duluth 323
Dulverton 6
Dumaguete 6
Dumbarton 19
Dumfries 34
Dumyat 1
Dunaharaszti 13
Dunajská Streda 18
Dunakeszi 11
Duncan 231
Duncannon 14
Duncanville 19
Dundalk 33
Dundas 7
Dundee 143
Dunedin 79
Dunfermline 14
Dung 16
Dungannon 18
Dungarvan 4
Dunkerque 6
Dunlap 13
Dunmow 10
Dunnellon 13
Duque De Caxias 41
Durango 71
Durban 315
Durg 3
Durgapur 195
Durham 747
Durrës 4
Durán 10
Dushanbe 36
Dussen 10
Duvall 28
Duxbury 6
Dyer 15
Dyersburg 30
Dzierzgon 12
Décines-charpieu 4
Dösjebro 18
Dülmen 7
Düren 25
Düsseldorf 259
Eagle 22
Eagle Mountain 11
Eagle Pass 15
Eagle River 12
Eagleby 10
Eaglemont 18
Earlham 9
Earlwood 40
Earth City 14
Easley 10
East Alton 4
East Amherst 47
East Aurora 28
East Bridgewater 18
East Brunswick 124
East Chicago 17
East Corinth 14
East Durham 6
East Elmhurst 17
East Falmouth 23
East Greenbush 23
East Greenwich 25
East Grinstead 12
East Haddam 5
East Hampton 31
East Hanover 18
East Hartford 64
East Haven 38
East Kilbride 10
Eas

Hawthorn 41
Hawthorne 79
Hayat 1
Hayden 15
Hayes 148
Haymarket 30
Hays 15
Hayward 291
Haywards Heath 25
Hazard 1
Hazel Crest 15
Hazel Park 12
Hazelwood 9
Hazerswoude-dorp 6
Hazlet 12
Hazleton 12
Heanor 14
Heart's Content 6
Heath 1
Heathfield 14
Hebei 177
Heber City 30
Hebertshausen 7
Hebron 7
Hechingen 12
Hecker 10
Heckmondwike 9
Hede 11
Hednesford 16
Heemstede 28
Heerhugowaard 10
Heerlen 19
Hefei 337
Heide 3
Heidelberg 239
Heidenheim 17
Heidesheim 13
Heilbronn 11
Heiligenhaus 7
Heiloo 9
Heimberg 7
Heiwajima 1
Helena 20
Helensburgh 5
Helensvale 10
Hellemmes 10
Hellenthal 11
Hellerup 37
Hellevoetsluis 20
Helmbrechts 12
Helmetta 12
Helmstedt 19
Helotes 19
Helsingborg 49
Helsinge 6
Helsinki 414
Helwan 12
Hem 9
Hemel Hempstead 70
Hemet 41
Hemhofen 8
Hemlock 11
Hempstead 134
Henderson 204
Hendersonville 94
Hendrik-ido-ambacht 23
Hengoed 27
Henley 7
Henley On Thames 2
Hennigsdorf 1
Hephzibah 13
Heraklion 95
Heras 17
Herblay 5
Hercules 18
Heredia 150
Hereford 15
Herent 15
Herentals 7
Heretaun

Les Eucalyptus 15
Les Lilas 11
Les Mureaux 21
Letchworth 29
Lethbridge 93
Leuchars 8
Leumeah 12
Leun 3
Leusden 5
Leuven 344
Levallois-perret 40
Levanger 12
Leven 32
Leverkusen 4
Levittown 93
Lewes 34
Lewis Center 19
Lewisburg 28
Lewisporte 5
Lewiston 93
Lewisville 72
Lexington 742
Lexington Park 28
Leyland 12
Leysin 7
Leça Do Balio 23
León 329
Liancourt 12
Liberec 33
Liberty 111
Liberty Lake 7
Libertyville 57
Libourne 21
Libreville 33
Licata 9
Lichfield 4
Lichnov 13
Lichtenfels 4
Lichtenstein 8
Lidcombe 7
Liden 3
Lidingö 5
Lidköping 4
Liedekerke 13
Lier 5
Lieusaint 9
Ligist 13
Lihue 18
Lilburn 84
Lille 119
Lille Skensved 13
Lillehammer 44
Lillestrøm 31
Lillian 15
Lillington 32
Lilongwe 43
Lilyfield 17
Lima 4533
Limassol 156
Limbiate 15
Limeira 49
Limerick 158
Limmen 15
Limoges 2
Limón 9
Linares 1
Linas 15
Lincoln 772
Lincoln City 24
Lincoln Park 9
Lincoln University 12
Lincolnshire 9
Lincolnton 22
Lincolnwood 20
Linden 47
Lindenhurst 9
Lindfield 52
Lindsay 18
Lindstrom 6
Lineville 8
Li

...

-94.7336 20
-94.7405 22
-94.773 16
-94.7786 10
-94.779 14
-94.7791 7
-94.7864 20
-94.7954 17
-94.7977 36
-94.7994 11
-94.8042 3
-94.8066 1
-94.8264 4
-94.8311 8
-94.8355 41
-94.8493 3
-94.8758 8
-94.8803 20
-94.8893 18
-94.8902 16
-94.8994 9
-94.9027 9
-94.933 11
-94.9473 15
-94.97 9
-94.9747 1
-94.9774 4
-94.9802 2
-94.9803 26
-94.986 5
-94.9894 7
-95.0035 22
-95.0167 5
-95.0185 2
-95.0194 13
-95.0273 37
-95.0278 15
-95.0578 11
-95.0841 4
-95.0898 19
-95.0918 3
-95.0949 52
-95.1091 3
-95.1105 2
-95.1124 3
-95.1273 3
-95.1277 14
-95.136 38
-95.1374 13
-95.1391 27
-95.1441 29
-95.1462 19
-95.1469 2
-95.1559 6
-95.1589 15
-95.1604 20
-95.1615 4
-95.1678 17
-95.1776 27
-95.1856 13
-95.1915 9
-95.1961 15
-95.201 71
-95.2034 8
-95.2043 15
-95.2199 4
-95.223 23
-95.2241 14
-95.2255 3
-95.2352 77
-95.2418 8
-95.2622 14
-95.2676 29
-95.2756 3
-95.2861 40
-95.2958 27
-95.3011 6
-95.3056 13
-95.31 18
-95.3139 24
-95.3201 14
-95.327 9
-95.3356 3
-95.337 70
-95.3379 6
-95.3436 46
-95.3454 4
-95.35

11.0667 4
11.0683 9
11.0833 16
11.0886 7
11.0911 8
11.1 13
11.1167 28
11.1185 12
11.1333 46
11.1358 4
11.1374 3
11.15 11
11.1667 15
11.1833 42
11.2 4
11.2154 8
11.2271 3
11.2333 22
11.2374 2
11.2392 15
11.2464 14
11.2485 4
11.25 199
11.2763 5
11.2833 23
11.3 38
11.3167 25
11.3212 13
11.3278 10
11.3294 5
11.3333 111
11.3387 86
11.3433 7
11.35 56
11.351 14
11.3541 10
11.3549 10
11.3665 11
11.3667 17
11.3755 24
11.3769 1
11.3833 13
11.3872 16
11.3914 3
11.4 87
11.4333 47
11.4433 3
11.4452 20
11.4629 6
11.4667 77
11.4724 7
11.5167 160
11.5182 14
11.5356 13
11.5401 10
11.55 13
11.5592 8
11.576 11
11.5833 1335
11.6 11
11.6167 4
11.6498 96
11.65 16
11.665 2
11.6667 13
11.6686 2
11.6833 13
11.6988 5
11.7 8
11.7159 12
11.7226 12
11.7319 10
11.7333 15
11.7358 15
11.75 7
11.7569 26
11.7833 29
11.7838 15
11.7842 4
11.7898 9
11.8014 10
11.8167 14
11.8456 1
11.85 10
11.8667 12
11.8833 94
11.9103 1
11.9106 5
11.9167 6
11.9294 43
11.9325 5
11.9333 23
11.9424 1
11.9639 2
11.9667 336
11.9668 63
11.9833 

152.9833 99
152.989 23
152.9904 41
152.9997 12
153.0 6
153.0004 31
153.0069 5
153.007 12
153.0135 7
153.0141 19
153.0199 2
153.0223 15
153.0234 37
153.0243 1568
153.0299 22
153.0305 8
153.031 15
153.0333 68
153.0343 24
153.0428 35
153.0458 8
153.05 8
153.0546 20
153.0547 3
153.0563 5
153.057 12
153.0583 25
153.0667 9
153.0777 13
153.0793 47
153.0912 32
153.0997 37
153.1 11
153.1103 7
153.1135 6
153.1246 21
153.15 4
153.1667 26
153.1833 39
153.2 4
153.2167 10
153.2333 2
153.26 1
153.3109 7
153.3289 10
153.3933 20
153.4 27
153.4123 6
153.4309 12
153.4333 17
153.4341 15
158.25 15
159.95 37
16.0 229
16.0113 10
16.0269 2
16.0757 1
16.0833 12
16.1 7
16.1167 8
16.1619 14
16.1667 18
16.1819 11
16.1833 25
16.1849 6
16.1913 5
16.2034 31
16.2167 9
16.2316 95
16.2333 13
16.25 48
16.2517 1
16.2667 66
16.2684 3
16.2833 7
16.3 32
16.3167 100
16.3317 16
16.3333 73
16.3378 23
16.3463 8
16.3472 10
16.3484 29
16.35 15
16.3501 23
16.3568 16
16.3575 13
16.3667 490
16.3696 84
16.37 104
16.3744 38
16.3924 27

34.9925 7
34.998 11
35.0 599
35.0078 11
35.039 262
35.05 11
35.1 7
35.1064 10
35.188 28
35.1903 53
35.2 251
35.2047 8
35.23 127
35.2406 2
35.25 56
35.2544 15
35.2652 6
35.2833 49
35.2956 17
35.3247 15
35.3289 77
35.3653 29
35.3711 1
35.3814 6
35.4853 64
35.5005 6
35.5097 830
35.5994 13
35.6156 9
35.6208 3
35.65 6
35.6725 12
35.7124 10
35.8333 93
35.9333 1003
36.0 281
36.0142 14
36.0667 23
36.0785 20
36.1436 7
36.1572 87
36.1873 24
36.2468 5
36.2478 1
36.2527 424
36.2659 25
36.2754 1
36.3 107
36.33 22
36.4706 4
36.5544 11
36.5547 13
36.58 6
36.5802 13
36.6101 4
36.6103 12
36.6833 50
36.7317 2
36.7331 2
36.7411 1
36.8167 1972
36.8475 3
36.9264 3
36.9833 5
37.0161 21
37.0833 4
37.0985 6
37.1667 1
37.2178 13
37.2731 26
37.2821 11
37.3181 17
37.3302 3
37.3333 5
37.349 9
37.3825 73
37.4297 3
37.5153 35
37.5331 49
37.5547 21
37.5563 11
37.5606 22
37.5895 2
37.615 299
37.6156 3788
37.6166 1066
37.6443 22
37.6716 10
37.7097 14
37.7339 28
37.7759 70
37.8256 4
37.8417 11
37.8575 20
37.8617 6
37.8

75.8167 989
75.8333 552
75.85 402
75.8833 7
75.9167 13
76.0167 2
76.05 3
76.0667 37
76.1167 17
76.1333 29
76.15 2
76.2167 207
76.2231 15
76.2333 353
76.25 9
76.2631 11
76.2667 3
76.2833 237
76.3275 31
76.3833 3
76.4 13
76.4003 241
76.45 39
76.4783 2
76.5 49
76.5167 166
76.5331 7
76.5333 9
76.5344 4
76.55 15
76.5531 15
76.5667 40
76.5833 9
76.5917 97
76.595 36
76.6 38
76.6167 20
76.6478 24
76.6497 221
76.6514 65
76.6667 49
76.6833 14
76.69 53
76.7808 104
76.7833 6
76.7933 996
76.8 10
76.8333 4
76.837 11
76.9 11
76.9167 43
76.9285 367
76.9333 12
76.9569 555
76.9614 458
76.9667 14
76.9681 23
76.9806 38
76.9833 60
77.0 9111
77.0167 9
77.0333 2857
77.0833 14
77.1 31
77.1017 10
77.1167 34
77.1722 85
77.1833 6
77.2 3570
77.2167 6708
77.2667 8
77.2833 27
77.3167 251
77.32 688
77.3333 18
77.35 50
77.4 626
77.4314 71
77.4333 511
77.55 90
77.5833 8805
77.6 29
77.6333 21
77.6833 21
77.7 93
77.7167 33
77.7333 111
77.75 12
77.7833 24
77.8167 51
77.85 10
77.8833 271
77.9333 1
77.95 48
78.0 1
78.0167 

In [41]:
print_missing_frequencies(original_records, location_cols)

cc_by_ip: 185572
countryLabel: 185572
continent: 183908
city: 310805
region: 346849
subdivision: 329645
postalCode: 677898
profile_country: 423056
latitude: 183908
longitude: 183908


Location Questions
* Might want to check that latitude and longitude are in the proper range. 

In [14]:
print_frequencies_col_group(un_cols)

un_major_region
 185572
Australia and New Zealand 21395
Caribbean 5841
Central America 21537
Central Asia 1798
Eastern Africa 10625
Eastern Asia 48912
Eastern Europe 39996
Melanesia 540
Micronesia 118
Middle Africa 1317
Northern Africa 17740
Northern America 335033
Northern Europe 58174
Polynesia 84
South America 64762
South-Eastern Asia 39758
Southern Africa 5857
Southern Asia 103877
Southern Europe 41203
Western Africa 14402
Western Asia 29223
Western Europe 52241

un_economic_group
 185572
Developed regions 555685
Developing_Nations 358748

un_developing_nation
 1083369
Least developed countries 16636

un_special_region
 974667
Latin America and the Caribbean 92140
Sub-Saharan-Africa 33198



In [29]:
print_missing_frequencies(original_records, un_cols)

un_major_region: 185572
un_economic_group: 185572
un_developing_nation: 1083369
un_special_region: 974667


UN Region Questons:
* No distinction between legitimate missing and not part of any of the categories. Could use `un_major_region` to get a "real" missing category and a "None of the Above" category. 

In [39]:
print_frequencies_col_group(other_cols)

mode
 7196
audit 480746
honor 597570
verified 14493

is_active
 7196
0 163879
1 928930

y1_anomalous
 1092793
1 7212

email_domain
013.net 5
10count.ca 3
126.COM 6
126.com 1893
139.com 59
163.COM 29
163.com 5162
1798consultants.com 15
189.cn 24
1on1ts.com 14
20mail.it 12
21cn.com 8
2200.com 10
2bcarquitectos.com 2
2kcreative.com 2
2ndacthealth.com 7
3-11.org 4
3000media.com 15
30wave.com 15
35000.co.za 12
365.um.edu.my 5
3alpha.us 5
3d.kipphouston.org 13
3fitness.com 12
3gvision.net 13
3i.com 2
3lcommunications.com 9
3mille.com 13
3z3.com 14
42itgroup.com 10
4GEN.biz 13
4ourth.net 10
4pmti.com 15
50can.org 8
562gmail.com 11
57yahoo.com 1
7heavensfoundation.org.za 11
8group.com.au 1
9-r.net 13
9netwave.com 13
9sight2020.com 3
ANU.EDU.AU 14
AOL.COM 45
AOL.com 37
ATLANTIC.EDU 10
AVIASPINE.COM 15
Alum.MIT.edu 6
Aol.com 4
Arkofus.com 7
AzfarRizvi.com 9
BELLSOUTH.NET 15
BTfinancialgroup.com 1
Bellagroup.com 14
Berlamont.com 1
Bluestone.com.au 4
Bsge.org 1
Bu.edu 6
CCF.ORG 13
CHOC.org 2
CJU.A

cedsgt.com 4
ceede.org.pe 8
cef-see.org 12
cefaonlus.it 14
cefg.cn 12
cegep-ste-foy.qc.ca 5
cegetel.net 16
cegiel.pl 4
ceips.org.au 3
celeritas.co.uk 8
cendra.org 12
centennialsd.org 12
center-labirint.si 14
central.edu 13
centrale-casablanca.ma 4
centralhealth.nl.ca 2
centrum.cz 88
centrum.sk 33
centurylink.net 15
centurytel.net 28
ceoexpress.com 1
cernet.com 14
ceruti.net 3
cesa6.org 28
cesaretti.org 8
cesvt.org 8
cetero.net 2
ceu.edu.ph 13
ceu.ox.ac.uk 12
ceunes.ufes.br 9
cevalogistics.com 11
cfbisd.edu 15
cfl.rr.com 37
cfree.com.au 3
cfs-australasia.com 9
cggs.act.edu.au 14
cgi.ac.th 8
cgiar.org 13
cgloo.com 6
cgocable.ca 33
cgtanalytics.com 3
cgtnet.dk 14
chadcoleman.me 9
chadgay.com 1
chadknowles.com 1
chadwickschool.org 13
chagrinschools.org 12
chaissoncreativeconsulting.com 10
chaitanyahospital.org 13
challiance.org 33
chalmers.se 6
championschools.org 9
champness.me.uk 8
chanceshafer.com 41
channeladvisor.com 5
channing.harvard.edu 51
chappuis.net 8
charite.de 45
charlescap.or

evoluciones.org 5
evolve-analytics.com 3
evotekrecruiting.com 8
ex.co.kr 5
ex.ua 12
exatec.itesm.mx 4
excarta.net 14
excelindia.com 14
excellus.com 1
excite.co.jp 21
excite.com 46
exemail.com.au 25
exerciseyourpotential.com.au 1
exeter.ac.uk 1
exeter.edu 21
exeter.ox.ac.uk 13
exhalegames.com 6
exigence.net 1
exit109.com 5
exlservice.com 2
exosomatics.com 6
expand-international.com 12
expeditors.com 12
experian.com 10
experienceinsight.co.uk 10
experienceworks.org.au 10
explodingpineapple.com 5
exrxhealth.com 3
ext.adclick.pt 6
extendhealth.com 13
ey.com 5
eyou.com 1
ezrasvoice.com 4
ezweb.ne.jp 43
f3pix.nl 3
f70.ca 10
fabdallasmag.com 12
facebook.com 123
factor-4.com 6
factor3.co.za 11
fagur.nl 5
faircentre.com.au 3
fairfaxcounty.gov 13
fairfield.edu 7
faithecho.com 14
faithgrowth.com 2
fakeinbox.com 12
familievonk.nl 7
familjekberg.se 8
familycareinc.org 3
fan.co.za 2
fandm.edu 25
fanrir.com 10
fantazy.me 15
fantex.com 10
farmacianacional.com.br 2
farmasi.uio.no 5
farva.net 5
fas.harv

jasonamyers.com 1
jato.com 6
javeriana.edu.co 42
javerianacali.edu.co 15
jawanpartners.com 1
jax.orf 8
jbedu.kr 4
jburroughs.org 11
jcit.co.za 15
jcky.ca 10
jcom.home.ne.jp 5
jcu.edu 5
jcu.edu.au 25
jd08.law.harvard.edu 7
jd14.law.harvard.edu 18
jd15.law.harvard.edu 22
jd16.law.harvard.edu 12
jd18.law.harvard.edu 11
jdainternational.org 6
jdanet.net 10
jdid.co 2
jdmillercpa.com 7
jeffames.org 5
jeffawaddell.com 6
jefferson.edu 3
jeffreyryan.org 14
jeffstateonline.com 4
jehosaphat.net 4
jellymail.net 14
jengphotos.com 1
jennmancini.com 9
jenroberts.co.uk 14
jeremiahcooper.com 9
jernigans.net 13
jerseyhost.net 14
jessicaglenarchitect.co.nz 10
jessup.edu 5
jetable.org 14
jff.org 6
jfrn.jus.br 8
jgifinancialservices.com 13
jhancock.com 16
jhhcvandermeijs.nl 7
jhmi.edu 47
jhsph.edu 17
jhu.edu 140
jhutsehai.org 10
jiangyixiao.com 18
jic.ac.uk 1
jigsawacademy.com 3
jimharber.com 4
jimmy.harvard.edu 25
jimmydixon.info 1
jimsadlermusic.com 6
jipmer.net 14
jjkeith.net 1
jjude.com 3
jkmetalurgica

mvcc.edu 6
mvd.biglobe.ne.jp 6
mvesystems.com 21
mvrht.com 37
mvrht.net 47
mvschool.com 24
mvuhu.co.za 3
mw.airtel.com 12
mweb.co.za 87
my.aci.k12.tr 3
my.athens.edu 11
my.bcit.ca 14
my.bridgeport.edu 5
my.bristol.ac.uk 33
my.chemeketa.edu 10
my.cityu.edu.hk 4
my.columbiasc.edu 8
my.costaatt.edu.tt 4
my.dom.edu 8
my.erau.edu 17
my.ethelwalker.org 15
my.fit.edu 12
my.fmi.unibuc.ro 1
my.fsu.edu 103
my.gvltec.edu 15
my.hamptonu.edu 1
my.hiram.edu 10
my.jcu.edu.au 17
my.liu.edu 12
my.maryvillecollege.edu 11
my.mcphs.edu 26
my.nd.edu.au 4
my.occc.edu 4
my.open.ac.uk 2
my.palmbeachstate.edu 10
my.smccd.edu 3
my.tccd.edu 27
my.tridenttech.edu 4
my.unitec.edu.mx 11
my.unt.edu 4
my.unthsc.edu 1
my.uri.edu 31
my.utsa.edu 13
my.uwstout.edu 14
my.waketech.edu 4
my.westminster.ac.uk 12
my.wheaton.edu 23
my.yorku.ca 21
myassociates.net 10
mybce.catholic.edu.au 8
mycit.ie 5
myconnection.co.za 12
mycosmos.gr 7
mycwi.cc 8
mydbs.ie 7
mydissolutelife.com 1
myemma.com 4
myfairpoint.net 28
mygccs.com 4
myh

rubem.net 12
rubenkuijper.nl 2
rubikit.com 4
ruc.edu.cn 35
rucigaj.com 6
rug.nl 23
rujak.org 7
rukovskaya.com 1
ruletheweb.co.uk 10
rulnick.com 6
rumcsi.org 5
runbox.com 22
runna.com.mx 12
ruralshores.com 1
ruri.waseda.jp 14
rusdlearns.net 12
rushsports.co.za 13
ruslansivak.com 15
rutgers.edu 37
ruwebby.com 12
rvschools.ab.ca 11
rw.globalcommunities.org 15
rwth-aachen.de 119
ryanandrobbie.com 11
ryanpowell.net 10
ryblr.com 3
ryerson.ca 44
s-spreiter.de 4
s3bi.de 2
s3geeks.com 14
s4.dion.ne.jp 4
s9d.co.uk 14
sa.gov.au 2
sabanciuniv.edu 49
saberce.com 8
sabesp.com.br 6
saboriocoto.com 1
sabrinazielinski.de 16
sach.org.sg 8
sadkhin.net 10
safian.gr 4
sagainnovations.org 10
sagepub.co.uk 15
sahrasahibi.com 9
saiglobal.com 8
sailingshipadventures.com 4
saint-gobain.com 2
saint-michaels.org 13
saintdenis.re 8
saintelizabeth.com 7
saintgeorge.do 12
saintwilfrids.com 5
saisd.net 13
sajt.cz 14
sakarya.edu.tr 10
saladyga.com 11
salamwatandar.com 2
salem.edu 14
salemstate.edu 3
salesforce.com 8
s

uc.edu 11
ucaldas.edu.co 9
ucalgary.ca 30
ucatolica.edu.co 16
ucb.com 8
ucc.ie 6
ucc.on.ca 5
uccs.edu 14
uccsimi.org 1
ucd.ie 1
ucdavis.edu 287
ucdconnect.ie 42
ucdenver.edu 71
ucdmc.ucdavis.edu 12
ucentral.cl 10
ucf.edu 9
ucfsd.net 1
uchc.edu 5
uchealth.org 8
uchicago.edu 121
uci.edu 95
ucl.ac.uk 131
ucl.cas.cz 2
ucla.edu 160
ucla.edu.ve 7
ucla.eud 9
uclabruins.com 2
uclaextension.edu 12
uclan.ac.uk 27
uclive.ac.nz 9
uclmail.net 15
uclouvain.be 36
ucm.cl 2
ucm.es 21
ucmerced.edu 37
uco.es 5
uco.net.co 12
ucol.mx 16
uconn.edu 52
ucop.edu 4
ucr.edu 21
ucsc.edu 69
ucsd.edu 85
ucsf.edu 6
ucsj.dk 7
ucsp.edu.pe 36
uct.ac.za 13
ucu.edu.uy 1
ucuenca.ec 14
ucvts.tec.nj.us 14
ud.edu.sa 7
udacity.com 3
udallas.edu 5
udc.es 25
udd.cl 1
udea.edu.co 15
udec.cl 38
udel.edu 77
udesa.edu.ar 15
udlap.mx 32
udld.biz 11
udo.edu 3
uds.edu.gh 5
udsd.org 4
ue.wroc.pl 5
uea.ac.uk 13
uef.fi 10
uem.br 10
uemail99.com 15
uet.edu.pk 12
uetpeshawar.edu.pk 3
uettaxila.edu.pk 4
ufc.br 15
ufh.ac.za 3
ufl.edu 87
ufm.

In [93]:
print_missing_frequencies(original_records, other_cols)

mode: 7196
is_active: 7196
y1_anomalous: 1092793
email_domain: 0


Misc Questions
* `y1_anomalous` might be tied to some missing data since the user "had to be side loaded from mongo"
* Email domain could use some cleaning - mostly forcing everything to lower case. 

*Numeric Fields*

We did not find any bad string values in expected numeric fields. Thus, we can cast those fields as float or integer for easier analysis of the fields.

In [10]:
def cast_as_int(theRecord, theCol):
    try:
        theRecord[theCol] = int(theRecord[theCol])
    except ValueError:
        theRecord[theCol] = None
        
def cast_as_float(theRecord, theCol):
    try:
        theRecord[theCol] = float(theRecord[theCol])
    except ValueError:
        theRecord[theCol] = None
        
def remove_none_frequencies(theFrequencies):
    if None in theFrequencies.keys():
        del theFrequencies[None]
    return theFrequencies
        
def get_min(theRecords, theCol):
    freqs = column_frequencies(theRecords, theCol)
    freqs_no_none = remove_none_frequencies(freqs)
    return min(freqs_no_none.keys())

def get_max(theRecords, theCol):
    freqs = column_frequencies(theRecords, theCol)
    freqs_no_none = remove_none_frequencies(freqs)
    return max(freqs_no_none.keys())

def get_range(theRecords, theCol):
    return (get_min(theRecords, theCol), get_max(theRecords, theCol))

In [11]:
# Cast appropriate fields as numeric
for record in original_records:
    cast_as_float(record, 'latitude')
    cast_as_float(record, 'longitude')
    cast_as_int(record, 'YoB')
    cast_as_float(record, 'grade')
    cast_as_float(record, 'passing_grade')
    cast_as_int(record, 'nevents')
    cast_as_int(record, 'ndays_act')
    cast_as_int(record, 'nplay_video')
    cast_as_int(record, 'nchapters')
    cast_as_int(record, 'nforum_posts')
    cast_as_int(record, 'nforum_votes')
    cast_as_int(record, 'nforum_endorsed')
    cast_as_int(record, 'nforum_threads')
    cast_as_int(record, 'nforum_comments')
    cast_as_int(record, 'nforum_pinned')
    cast_as_int(record, 'nprogcheck')
    cast_as_int(record, 'nproblem_check')
    cast_as_int(record, 'nforum_events')
    cast_as_int(record, 'language_brwsr_nevents')
    cast_as_int(record, 'language_brwsr_ndiff')
    cast_as_int(record, 'language_download')
    cast_as_int(record, 'language_nevents')
    cast_as_int(record, 'language_ndiff')
    cast_as_int(record, 'ntranscript')
    cast_as_int(record, 'nshow_answer')
    cast_as_int(record, 'nvideo')
    cast_as_int(record, 'nvideos_unique_viewed')
    cast_as_float(record, 'nvideos_total_watched')
    cast_as_int(record, 'nseq_goto')
    cast_as_int(record, 'nseek_video')
    cast_as_int(record, 'npause_video')
    cast_as_float(record, 'avg_dt')
    cast_as_float(record, 'sdv_dt')
    cast_as_float(record, 'max_dt')
    cast_as_float(record, 'n_dt')
    cast_as_float(record, 'sum_dt')

Look at Ranges of Numeric Values

In [92]:
quant_cols = ['latitude', 'longitude', 'YoB', 'grade', 'passing_grade', 
              'nevents', 'ndays_act', 'nplay_video', 'nchapters', 'nforum_posts', 'nforum_votes', 'nforum_endorsed', 
              'nforum_threads', 'nforum_comments', 'nforum_pinned', 'nprogcheck', 'nproblem_check', 'nforum_events', 
              'language_brwsr_nevents', 'language_brwsr_ndiff', 'language_nevents', 'language_ndiff', 'ntranscript', 
              'nshow_answer', 'nvideo', 'nvideos_unique_viewed', 'nvideos_total_watched', 'nseq_goto', 'nseek_video', 
              'npause_video', 'avg_dt', 'sdv_dt', 'max_dt', 'n_dt', 'sum_dt']

for col in quant_cols:
    print("{}: {}".format(col, get_range(original_records, col)))

latitude: (-54.8, 71.285)
longitude: (-175.2018, 178.4167)
YoB: (1893, 2018)
grade: (0.0, 1.15)
passing_grade: (0.5, 0.97)
nevents: (1, 234385)
ndays_act: (1, 2475)
nplay_video: (0, 90057)
nchapters: (1, 34)
nforum_posts: (1, 299)
nforum_votes: (0, 224)
nforum_endorsed: (0, 30)
nforum_threads: (0, 142)
nforum_comments: (0, 281)
nforum_pinned: (0, 31)
nprogcheck: (0, 643)
nproblem_check: (0, 26367)
nforum_events: (0, 17829)
language_brwsr_nevents: (1, 114745)
language_brwsr_ndiff: (1, 8)
language_nevents: (1, 6051)
language_ndiff: (1, 10)
ntranscript: (0, 4346)
nshow_answer: (0, 3432)
nvideo: (0, 90057)
nvideos_unique_viewed: (1, 363)
nvideos_total_watched: (0.0022371364653243847, 6.5)
nseq_goto: (0, 6941)
nseek_video: (0, 10398)
npause_video: (0, 57069)
avg_dt: (0.0, 299.589759)
sdv_dt: (0.0, 209.66384207378675)
max_dt: (0.0, 300.0)
n_dt: (0.0, 233917.0)
sum_dt: (0.0, 2895426.074810009)


Observations
* Some variables start at 1 while others at 0. Looks like for some, 0 is considered missing. What's the difference between 0 and missing for those that have both?

#### Repairing Values

*Cleaning Email Domain*

We want  the email domain variable to hold completely lower-case strings for proper grouping.

In [48]:
for record in original_records:
    record['email_domain'] = record['email_domain'].lower()

*Looking for missing or correct values in duplicates*

In [75]:
def get_unique_users(theRecords):
    total_records = 0
    unique_users = 0
    users_seen = set()

    for record in theRecords:
        total_records += 1
        key = record['user_id']
        if key not in users_seen:
            users_seen.add(key)
            unique_users += 1
    return total_records, unique_users, users_seen

def get_unique_users_courses(theRecords):
    total_records = 0
    unique_pairs = 0
    pairs_seen = set()

    for record in theRecords:
        total_records += 1
        key = get_key(record)
        if key not in pairs_seen:
            pairs_seen.add(key)
            unique_pairs += 1
    return total_records, unique_pairs, pairs_seen

def get_user(thePair):
    return thePair[0]

def get_course(thePair):
    return thePair[1]

def get_user_course(theRecord):
    return (theRecord['user_id'], theRecord['course_id'])

# What are demographic fields that we expect to be the same across courses for a user?
# Year of Birth, Gender (If we assume no one is transitioning genders between courses)

def get_missing_or_none_array(theRecord):
    missing_array = np.zeros((1, len(theRecord.keys())))
    for i, key in enumerate(theRecord.keys()):
        if theRecord[key] == '' or theRecord[key] == None:
            missing_array[0, i] = 1
    return missing_array

def get_sum_missing_pairs(theRecords, thePair):
    sums = []
    for record in grouped_records[thePair]:
        missings = get_missing_or_none_array(record)
        sums.append(np.sum(missings))
    return sums

In [15]:
total_records, unique_users_n, dup_users_n, unique_user_ids = get_unique_users(original_records)

In [24]:
total_records, unique_pairs_n, unique_pairs = get_unique_users_courses(original_records)

In [35]:
sorted_pairs = sorted(unique_pairs, key = get_user)

In [40]:
sorted_records = sorted(original_records, key = get_user_course)

In [92]:
previous_key = ('', '')
grouped_records = {}
current_records = []

for i, record in enumerate(original_records):
    current_key = (record['user_id'], record['course_id'])
    if i == (len(original_records) - 1):
        current_records.append(record)
        grouped_records[previous_key] = current_records
    elif current_key == previous_key:
        current_records.append(record)
    elif previous_key == ('', ''):
        current_records = []
        previous_key = current_key
    else:
        grouped_records[previous_key] = current_records
        current_records = []
        previous_key = current_key

In [94]:
for pair in sorted_pairs:
    missing_sums = (get_sum_missing_pairs(grouped_records, pair))
    result = all(element == missing_sums[0] for element in missing_sums)
    if result == False:
        print("Different Missing")
        print(pair)

Looks like all the duplicates are the same! (Or at least have the same amount of missing values.) Thus, we can't use the duplicates to fill in potential missing values. We will have to repair values some other way.